In [1]:
import pandas as pd
import numpy as np
import joblib
import os
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split, cross_val_score, cross_val_predict
import matplotlib.pyplot as plt
import altair as alt
from interpret.glassbox import ExplainableBoostingRegressor,ExplainableBoostingClassifier,LinearRegression, RegressionTree
from interpret.data import Marginal
from interpret.perf import RegressionPerf
import sys
sys.path.append("../../../utils/")
# Import custom pkgs
import utils
from ebm_util import tabularize_global_explanation, tabularize_local_explanation
from ebm_chart_util import y_dist_figure, feature_importance_figure, ebm_pdp_figure, contribution_figure, ebm_score_figure

In [2]:
data_path = '../../../data/wine_quality/raw/wine_quality.csv'
df = pd.read_csv(data_path)
display(df.head(3))

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5

In [3]:
print("Size of dataset: {} ".format(df.shape))

Size of dataset: (1599, 12) 


In [4]:
ebm = ExplainableBoostingRegressor(interactions=0, random_state=42) # no interaction terms
ebm.fit(df.iloc[:,:-1], df.quality)

# model_path = '../../../data/wine_quality/model/wine_quality_ebm_wip.pkl'
# joblib.dump(ebm, model_path)
# ebm = joblib.load(model_path)

ExplainableBoostingRegressor(feature_names=['fixed acidity', 'volatile acidity',
                                            'citric acid', 'residual sugar',
                                            'chlorides', 'free sulfur dioxide',
                                            'total sulfur dioxide', 'density',
                                            'pH', 'sulphates', 'alcohol'],
                             feature_types=['continuous', 'continuous',
                                            'continuous', 'continuous',
                                            'continuous', 'continuous',
                                            'continuous', 'continuous',
                                            'continuous', 'continuous',
                                            'continuous'],
                             interactions=0)

In [8]:
dictionary = {'영문명': ['fixed acidity','volatile acidity','citric acid','residual sugar',
                            'chlorides','free sulfur dioxide','total sulfur dioxide','density',
                            'pH','sulphates','alcohol','quality'],
                '한글명':['고정산도','휘발성산도','구연산','잔류설탕', '염화물', '자유황산', '총이산화황',
                        '밀도', 'pH', '황산염', '알코올', '품질'],
                '설명': ['포도주에 고정되어 있는 산미 정도',
                        '높은 수준에서는 불쾌한 식초 맛을 초래할 수 있는 와인의 아세트산의 양',
                        '소량으로 발견되는 경우 와인에 신선함과 맛을 추가하는 구연산 양', 
                        '와인 발효 후 잔류하는 설탕의 양',
                        '와인에 들어있는 소금의 양', 
                        '미생물 성장과 포도주의 산화를 방지하는 황산 값',
                        '자유 황산 등으로 인해 생기는 이산화황, 저농도에서 거의 검출되지 않으나 50ppm 이상에서는 이산화황의 향과 맛이 느껴짐',
                        '알코올과 설탕 퍼센트 함량으로 결정됨',
                        '와인의 산성, 염기성 정도. 대부분의 와인은 pH 가늠자에 3~4에 있음',
                        '와인 첨가제로서 항균 및 항산화 작용 수행',
                        '와인의 알콜 함량 퍼센트',
                        '와인에 대한 평가 점수 (0~10)']}
                    
dict_df = pd.DataFrame(data=dictionary, columns=['영문명', '한글명', '설명'])
dict_df
# joblib.dump(dict_df, '../../../data/wine_quality/processed/wine_quality_data_dict.pkl')

영문명    한글명  \
0          fixed acidity   고정산도   
1       volatile acidity  휘발성산도   
2            citric acid    구연산   
3         residual sugar   잔류설탕   
4              chlorides    염화물   
5    free sulfur dioxide   자유황산   
6   total sulfur dioxide  총이산화황   
7                density     밀도   
8                     pH     pH   
9              sulphates    황산염   
10               alcohol    알코올   
11               quality     품질   

                                                   설명  
0                                  포도주에 고정되어 있는 산미 정도  
1             높은 수준에서는 불쾌한 식초 맛을 초래할 수 있는 와인의 아세트산의 양  
2                 소량으로 발견되는 경우 와인에 신선함과 맛을 추가하는 구연산 양  
3                                  와인 발효 후 잔류하는 설탕의 양  
4                                      와인에 들어있는 소금의 양  
5                          미생물 성장과 포도주의 산화를 방지하는 황산 값  
6   자유 황산 등으로 인해 생기는 이산화황, 저농도에서 거의 검출되지 않으나 50ppm...  
7                                알코올과 설탕 퍼센트 함량으로 결정됨  
8            와인의 산성, 염기성 정도. 대부분의 와인은 pH 가늠자에 3~4에 있음  
9                             와인 첨가제로서 항균 및 항산화 작용 수행  
10                                      와인의 알콜 함량 퍼센트  
11                                와인에 대한 평가 점수 (0~10)

In [7]:
# y distribution figure
fig = y_dist_figure(df, 'quality', 40, '와인 Quality')
fig.interactive()

alt.Chart(...)

In [10]:
df_feature_importance = utils.tabularize_feature_importance(df.iloc[:,:-1], ebm)
df_feature_importance.sort_values(by='importance', ascending=False, inplace=True)
fig = feature_importance_figure(df_feature_importance, 20)
fig.interactive()

alt.Chart(...)

In [11]:
feature_top4 = df_feature_importance[:4].feature.tolist()
global_df = tabularize_global_explanation(df.iloc[:,:-1], ebm)

for i in range(0,4):
    fig = ebm_pdp_figure(df, feature_top4[i], global_df, 150, 150)
    fig.display()

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

In [12]:
instance = 1
local_df = tabularize_local_explanation(df.iloc[:,:-1], df.quality, ebm)
waterfall = contribution_figure(df, local_df, instance, 200, 450)
waterfall.display()

alt.LayerChart(...)

In [13]:
feature_list = df.iloc[:,:-1].columns.tolist()

for i in range(len(feature_list)):
    fig = ebm_score_figure(df, feature_list[i], global_df, local_df, instance, 150, 150)
    fig.display()

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

...

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)

alt.LayerChart(...)